## Interactive map creation notebook

#### Final interactive map displays traffic volumes for street sections and street network in Helsinki area.

** **

**Traffic volumes data:** Daily average of total motor vehicle flow in some street parts in Helsinki in 2019.

Source: Traffic volumes in CSV. https://hri.fi/data/en_GB/dataset/liikennemaarat-helsingissa
Traffic data from Helsinki. The maintainer of the dataset is Helsingin kaupunkiympäristön toimiala / Liikenne- ja katusuunnittelu. The dataset has been downloaded from Helsinki Region Infoshare service on 02.12.2021 under the license Creative Commons Attribution 4.0.
- Data contains daily average volumes of motor vehicles each autumn from 2010 onwards. Motor vehicles include passenger cars, vans, trucks, lorries, busses and motor bikes.
- Note: original csv file had to be saved with UTF-8 encoding before use

** **

**Street network data and Sea area data**

Data is derived from City of Helsinki WFS-service.

Source and information about the data (in Finnish): https://www.hel.fi/helsinki/fi/kartat-ja-liikenne/kartat-ja-paikkatieto/Paikkatiedot+ja+-aineistot/avoimet+paikkatiedot/

Data used to create the  map:
- Main roads (Seutukartta_liikenne_paatiet)
- Road network (Seutukartta_liikenne_tiesto)
- Sea area (Seutukartta_maankaytto_merialue)

In [1]:
# Import needed modules
import pandas as pd
import matplotlib.pyplot as plt
import geopandas as gpd
from pyproj import CRS
import folium

In [2]:
# Read in traffic volume data
traf_fp = "hki_liikennemaarat.csv"
traffic = pd.read_csv(traf_fp, sep=";")

# Inspect data
traffic.head()

piste                nimi    x_gk25   y_gk25  suunta  aika  vuosi  ha  pa  \
0   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0     0   2010  60   4   
1   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   100   2010  35   3   
2   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   200   2010  17   1   
3   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   300   2010  17   1   
4   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   400   2010  36   2   

   ka  ra  la  mp  rv  autot  
0   1   0   4   0   0     69  
1   1   0   2   0   0     41  
2   0   0   1   0   0     19  
3   0   0   1   0   0     19  
4   0   0   2   0   0     40

In [3]:
# Convert traffic data into GeoDataFrame
traffic = gpd.GeoDataFrame(traffic, geometry=gpd.points_from_xy(traffic.x_gk25, traffic.y_gk25))

# Select latest available year for analysis (2019)
traffic = traffic.loc[(traffic['vuosi'] == 2019)]

# Check result
traffic.head()

piste                nimi    x_gk25   y_gk25  suunta  aika  vuosi  ha  \
43092   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0     0   2019  22   
43093   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   100   2019  20   
43094   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   200   2019  21   
43095   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   300   2019  16   
43096   A01  LAUTTASAAREN SILTA  25494426  6672169     1.0   400   2019  16   

       pa  ka  ra  la  mp  rv  autot                          geometry  
43092   1   0   0   1   0   0     24  POINT (25494426.000 6672169.000)  
43093   2   0   0   1   0   0     23  POINT (25494426.000 6672169.000)  
43094   1   0   0   1   0   0     23  POINT (25494426.000 6672169.000)  
43095   1   0   0   1   0   0     18  POINT (25494426.000 6672169.000)  
43096   1   0   0   1   0   0     18  POINT (25494426.000 6672169.000)

In [4]:
"""
Calculate total motor vehicle flow for each street section.
-> sum of all vehicles passing that section daily on average 
"""

# Summarize traffic volumes by street section ID ("piste")
grouped = traffic.groupby(['piste'])['autot'].sum().reset_index()

# Dissolve = 1 row for each street section
traf_diss = traffic.dissolve(by='piste').reset_index()

# Join total traffic volumes to street section information
joined = pd.merge(traf_diss, grouped, left_index=True, right_index=True)

# Select relevant columns for further processing
joined = joined[['piste_y', 'autot_y', 'geometry']]

# Change CRS to WGS84 for further visulization
joined.crs = CRS.from_epsg(3879)
joined = joined.to_crs(CRS.from_epsg(4326))

# Create separate location columns
joined['lon'] = joined['geometry'].x
joined['lat'] = joined['geometry'].y

#### 
**Check that data processing above was valid. Traffic data should contain one row for each street section/point**

In [5]:
grouped.head(2)

piste  autot
0   A01  10623
1   A02  52013

In [6]:
traf_diss.head(2)

piste                          geometry                nimi    x_gk25  \
0   A01  POINT (25494426.000 6672169.000)  LAUTTASAAREN SILTA  25494426   
1   A02  POINT (25494579.000 6672693.000)   LAPINLAHDEN SILTA  25494579   

    y_gk25  suunta  aika  vuosi  ha  pa  ka  ra  la  mp  rv  autot  
0  6672169     1.0     0   2019  22   1   0   0   1   0   0     24  
1  6672693     1.0     0   2019  93   5   1   1   5   0   0    105

In [7]:
joined.head(2)

piste_y  autot_y                   geometry        lon        lat
0     A01    10623  POINT (24.89962 60.16239)  24.899615  60.162385
1     A02    52013  POINT (24.90236 60.16709)  24.902357  60.167091

In [8]:
"""
Read in data layers from WFS-service.
Keep only needed columns.
Change CRS´s to WGS84 for visualization.
Remove rows with empty geometry.
"""

# Main roads
url = "https://kartta.hel.fi/ws/geoserver/avoindata/wfs?SERVICE=WFS&VERSION=1.1.0&REQUEST=GetFeature&TYPENAME=avoindata:Seutukartta_liikenne_paatiet&OUTPUTFORMAT=json"
roads = gpd.read_file(url)
roads = roads[['geometry', 'nimi', 'tieluokka_nro']]

roads = roads[roads.geometry != None]
roads = roads.to_crs(CRS.from_epsg(4326))

# Road network
url = "https://kartta.hel.fi/ws/geoserver/avoindata/wfs?SERVICE=WFS&VERSION=1.1.0&REQUEST=GetFeature&TYPENAME=avoindata:Seutukartta_liikenne_tiesto&OUTPUTFORMAT=json"
roads_all = gpd.read_file(url)
roads_all = roads_all[['geometry', 'nimi', 'tieluokka_nro']]

roads_all = roads_all[roads_all.geometry != None]
roads_all = roads_all.to_crs(CRS.from_epsg(4326))


# Sea area
url = "https://kartta.hel.fi/ws/geoserver/avoindata/wfs?SERVICE=WFS&VERSION=1.1.0&REQUEST=GetFeature&TYPENAME=avoindata:Seutukartta_maankaytto_merialue&OUTPUTFORMAT=json"
sea = gpd.read_file(url)
sea = sea['geometry']
sea = sea.to_crs(CRS.from_epsg(4326))

In [9]:
# Check that data´s CRS´s match
roads.crs == sea.crs == joined.crs

True

In [10]:
"""Plot the map"""

# Use folium for visualization without background map
m = folium.Map(location=[60.24, 24.9], tiles=None, zoom_start=11, control_scale=True)

# Add sea area
folium.Choropleth(
    sea, 
    fill_opacity=0.5,
    fill_color='grey',
    line_weight=0
    ).add_to(m)

# Add main roads
folium.Choropleth(
    roads[roads.geometry.length>0.0000001],
    line_weight=2.3,
    line_color='white'
    ).add_to(m)

# Add road network
folium.Choropleth(
    roads_all[roads_all.geometry.length>0.0000001],
    line_weight=1,
    line_color='white'
    ).add_to(m)

# Visualize traffic volumes using circles
for i in range(0,len(joined)):
   folium.Circle(
      location=[joined.iloc[i]['lat'], joined.iloc[i]['lon']],
      popup=joined.iloc[i]['autot_y'],
    # Size of circle depends on traffic volume
      radius=int(joined.iloc[i]['autot_y'])*0.01,
      color='darkred',
      fill=True,
      fill_color='darkred'
   ).add_to(m)

# Add information popup
text = 'Daily average of total motor vehicle flow in some street parts in Helsinki in 2019. Data by City of Helsinki. Click a circle to show exact traffic volume.'
iframe = folium.IFrame(text, width=300, height=100)
popup = folium.Popup(iframe, max_width=3000)
Text = folium.Marker(location=[60.205, 25.02], popup=popup,
                     icon=folium.Icon(icon_color='darkred'))
m.add_child(Text)

# Display the map
m

<ipython-input-10-d141ed174ab7>:16: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  roads[roads.geometry.length>0.0000001],
<ipython-input-10-d141ed174ab7>:23: UserWarning: Geometry is in a geographic CRS. Results from 'length' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  roads_all[roads_all.geometry.length>0.0000001],


In [11]:
# Create output as html file
outfp = "interactive_map.html"
m.save(outfp)